In [ ]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import MinMaxScaler
from sklearn.decomposition import PCA
from sklearn.cluster import KMeans
from sklearn.cluster import DBSCAN
from sklearn.cluster import HDBSCAN
from sklearn.neighbors import NearestNeighbors
from sklearn.metrics import silhouette_score
import matplotlib.pyplot as plt
import altair as alt
import seaborn as sns
alt.data_transformers.disable_max_rows()

In [ ]:
df = pd.read_csv('SO_ML_2022_cleaned.csv')
df = df.drop(columns=['Unnamed: 0'])
# add column for mass flow
df['Mass_flow_rate'] = df['velocity']*df['density']
df_so_data = df.copy()
df.head()

fractional_year  O7_O6_ratio  C6_C4_ratio  C6_C5_ratio  Fe_O_ratio  \
0      2022.049316     0.089865     2.458390     0.444265    0.150213   
1      2022.049335     0.083158     2.841864     0.410422    0.160867   
2      2022.049354     0.098469     2.527932     0.328493    0.132257   
3      2022.049373     0.070984     2.794871     0.356665    0.135882   
4      2022.049392     0.078036     1.416381     0.329367    0.154701   

   O_ave_charge  velocity  density  Mass_flow_rate  
0      6.074951   494.797  2.82344     1397.029642  
1      6.072842   489.727  2.96590     1452.481309  
2      6.086165   491.465  2.65348     1304.092548  
3      6.060820   490.259  2.89073     1417.206399  
4      6.068972   493.497  2.96546     1463.445614

### Preprocessing

In [ ]:
# scale the data using min/max scaler
cols = df.columns.tolist()[1:]
scaler = MinMaxScaler()
data_scaled = scaler.fit_transform(df[cols])


### PCA

In [ ]:
pca = PCA(n_components=3)
data_pca = pca.fit_transform(data_scaled)
df_pca = pd.DataFrame(data_pca, columns=['PC1', 'PC2', 'PC3'])

## HDBSCAN

In [ ]:
min_cluster_size = [100, 200, 500, 1000]
cluster_selection_epsilon = [0.05, 0.06, 0.07, 0.08, 0.09]
cluster_selection_method = ['eom', 'leaf']

min_cluster_size_to_df = []
cluster_selection_epsilon_to_df = []
cluster_selection_method_to_df = []
num_clusters_to_df = []
sil_scores_to_df = []

for mcs in min_cluster_size:
    for cse in cluster_selection_epsilon:
        for csm in cluster_selection_method:
            hdb = HDBSCAN(min_cluster_size=mcs, cluster_selection_epsilon=cse, cluster_selection_method=csm).fit(df_pca)
            num_labels = len(set(hdb.labels_))
            if num_labels == 1:
                num_clusters_to_df.append(num_labels)
                sil_scores_to_df.append(math.nan)
                min_cluster_size_to_df.append(mcs)
                cluster_selection_epsilon_to_df.append(cse)
                cluster_selection_method_to_df.append(csm)
            else:
                num_clusters_to_df.append(num_labels)
                sil_scores_to_df.append(silhouette_score(df_pca, hdb.labels_))
                min_cluster_size_to_df.append(mcs)
                cluster_selection_epsilon_to_df.append(cse)
                cluster_selection_method_to_df.append(csm)

df_param_search = pd.DataFrame(zip(min_cluster_size_to_df, cluster_selection_epsilon_to_df, cluster_selection_method_to_df, num_clusters_to_df, sil_scores_to_df), 
                               columns=['min_cluster_size', 'cluster_selection_epsilon', 'cluster_selection_method', 'num_clusters', 'silhouette_score'])

df_param_search.sort_values(by=['silhouette_score'], ascending=False).head(3)

min_cluster_size  cluster_selection_epsilon cluster_selection_method  \
0               100                       0.05                      eom   
2               100                       0.06                      eom   
3               100                       0.06                     leaf   

   num_clusters  silhouette_score  
0             3          0.302025  
2             3          0.302025  
3             3          0.302025

In [ ]:
hdb = HDBSCAN(min_cluster_size=100, cluster_selection_epsilon=0.05, cluster_selection_method='leaf').fit(df_pca)
# hdb = HDBSCAN(min_cluster_size=200).fit(data_scaled)
# data_scaled
labels = hdb.labels_

df_pca_labelled = df_pca.copy()
df_pca_labelled['Cluster_Label'] = labels
df_pca_labelled['Cluster_Label'] = df_pca_labelled.Cluster_Label.astype('category')

df_so_data_labelled = df_so_data.copy()
df_so_data_labelled['Cluster_Label'] = labels
df_so_data_labelled['Cluster_Label'] = df_so_data_labelled.Cluster_Label.astype('category')

print(f"The silhouette score of the final model is: {silhouette_score(df_pca, labels)}")

The silhouette score of the final model is: 0.3020250314560404


In [ ]:
chart1 = alt.Chart(df_pca_labelled).mark_circle().encode(
    x='PC1',
    y='PC2',
    color='Cluster_Label'
)

chart2 = alt.Chart(df_pca_labelled).mark_circle().encode(
    x='PC2',
    y='PC3',
    color='Cluster_Label'
)

chart3 = alt.Chart(df_pca_labelled).mark_circle().encode(
    x='PC1',
    y='PC3',
    color='Cluster_Label'
)

chart1 | chart2 | chart3

alt.HConcatChart(...)

In [ ]:
features = df_so_data_labelled.columns[1:-1].tolist()
charts = []
for feature in features:
    y_var = 'mean(' + feature + ')'
    chart = alt.Chart(df_so_data_labelled).mark_bar().encode(
        x='Cluster_Label:O',
        y=alt.Y(y_var)
    ).properties(
        width = 100,
        height = 300
    )

    error_bars = alt.Chart(df_so_data_labelled).mark_errorbar(extent='stderr').encode(
        x='Cluster_Label',
        y=feature
    )

    chart = alt.layer(chart, error_bars)
    charts.append(chart)
alt.hconcat(*charts)

alt.HConcatChart(...)